### Imports

In [1]:
import pandas as pd
import json
import os, sys
from tqdm import tqdm
import numpy as np
import polars as pl
from polars import col as c
from pprint import pprint
import matplotlib.pyplot as plt
import re
import shap

sys.path.append("../")
pl.Config.set_tbl_rows(50)

# explicitly require this experimental feature
from sklearn.experimental import enable_iterative_imputer  # noqa

# now you can import normally from sklearn.impute
from sklearn.impute import IterativeImputer
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import train_test_split
from catboost import CatBoostRegressor, CatBoostClassifier

### constants

In [2]:
FILES_DIR = "../data"

### select data

In [3]:
# os.path.join(FILES_DIR, path)

In [4]:
path = "data_for_models"
os.makedirs(os.path.join(FILES_DIR, path), exist_ok=True)
file_name = "epic_records_with_target.parquet"
file_path = os.path.join(FILES_DIR, path, file_name)
epic_records_with_target = pl.read_parquet(file_path)

In [6]:
epic_records_with_target["target"].value_counts()

shape: (2, 2)
┌────────┬───────┐
│ target ┆ count │
│ ---    ┆ ---   │
│ i32    ┆ u32   │
╞════════╪═══════╡
│ 1      ┆ 474   │
│ 0      ┆ 517   │
└────────┴───────┘

In [5]:
epic_records_with_target.sample(2)

shape: (2, 210)
┌────────────┬─────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ patient_id ┆ gender  ┆ amnez_lif ┆ amnez_dis ┆ … ┆ secondary ┆ secondary ┆ secondary ┆ secondary │
│ ---        ┆ ---     ┆ e         ┆ ease      ┆   ┆ _disease_ ┆ _disease_ ┆ _disease_ ┆ _disease_ │
│ str        ┆ str     ┆ ---       ┆ ---       ┆   ┆ D13       ┆ N40       ┆ M19       ┆ M42       │
│            ┆         ┆ str       ┆ str       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│            ┆         ┆           ┆           ┆   ┆ i64       ┆ i64       ┆ i64       ┆ i64       │
╞════════════╪═════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ 04E4942E-8 ┆ Мужской ┆ АНАМНЕЗ   ┆ АНАМНЕЗ   ┆ … ┆ 0         ┆ 0         ┆ 0         ┆ 0         │
│ 894-4BA9-9 ┆         ┆ ЖИЗНИ:    ┆ ЗАБОЛЕВАН ┆   ┆           ┆           ┆           ┆           │
│ 04B-AE15BB ┆         ┆           ┆ ИЯ  ПОВЫШ ┆   ┆           ┆           ┆           ┆           │
│ …          ┆         ┆           ┆ ЕНИЕ…     ┆   ┆           ┆           ┆           ┆           │
│ 78980274-A ┆ Мужской ┆ АНАМНЕЗ   ┆ АНАМНЕЗ   ┆ … ┆ 0         ┆ 0         ┆ 0         ┆ 0         │
│ CE7-4B47-9 ┆         ┆ ЖИЗНИ:    ┆ ЗАБОЛЕВАН ┆   ┆           ┆           ┆           ┆           │
│ 802-74ACE7 ┆         ┆           ┆ ИЯ  ИМ -  ┆   ┆           ┆           ┆           ┆           │
│ …          ┆         ┆           ┆ РАНЕ…     ┆   ┆           ┆           ┆           ┆           │
└────────────┴─────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [6]:
train_data = (
    epic_records_with_target.select(
        # "admission_datetime",
        "gospitalisation_type",
        "gospitalisation_delivery",
        # "following_admission_datetimes",
        "gender",
        "has_competing_disease",
        "gospitalization_result",
        "main_desease_status",
        "condition_status",
        "age",
        "heart_rate",
        "BMI",
        "right atrium",
        "secondary_and_background_disease_count",
        pl.selectors.starts_with("main_disease_I"),  # type of main disease
        pl.selectors.matches("secondary_disease_\D\d\d"),  # type of secondary disease
        "target",
    )
    # ["main_desease_status"].value_counts()
)
train_data.sample(3)

<>:18: SyntaxWarning: invalid escape sequence '\D'
<>:18: SyntaxWarning: invalid escape sequence '\D'
/var/folders/v_/vqhfnf3s4sb7g6nfby7hc9sr0000gn/T/ipykernel_91389/306947988.py:18: SyntaxWarning: invalid escape sequence '\D'
  pl.selectors.matches("secondary_disease_\D\d\d"),  # type of secondary disease


shape: (3, 192)
┌────────────┬────────────┬─────────┬────────────┬───┬────────────┬───────────┬───────────┬────────┐
│ gospitalis ┆ gospitalis ┆ gender  ┆ has_compet ┆ … ┆ secondary_ ┆ secondary ┆ secondary ┆ target │
│ ation_type ┆ ation_deli ┆ ---     ┆ ing_diseas ┆   ┆ disease_N4 ┆ _disease_ ┆ _disease_ ┆ ---    │
│ ---        ┆ very       ┆ str     ┆ e          ┆   ┆ 0          ┆ M19       ┆ M42       ┆ i32    │
│ str        ┆ ---        ┆         ┆ ---        ┆   ┆ ---        ┆ ---       ┆ ---       ┆        │
│            ┆ str        ┆         ┆ i32        ┆   ┆ i64        ┆ i64       ┆ i64       ┆        │
╞════════════╪════════════╪═════════╪════════════╪═══╪════════════╪═══════════╪═══════════╪════════╡
│ Первичный  ┆ Плановая   ┆ Мужской ┆ 0          ┆ … ┆ 0          ┆ 0         ┆ 0         ┆ 1      │
│            ┆ госпитализ ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
│            ┆ ация       ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
│ Первичный  ┆ Доставлен  ┆ Мужской ┆ 0          ┆ … ┆ 0          ┆ 0         ┆ 0         ┆ 1      │
│            ┆ бригадой   ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
│            ┆ скорой     ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
│            ┆ помо…      ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
│ Первичный  ┆ Плановая   ┆ Мужской ┆ 0          ┆ … ┆ 0          ┆ 0         ┆ 0         ┆ 1      │
│            ┆ госпитализ ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
│            ┆ ация       ┆         ┆            ┆   ┆            ┆           ┆           ┆        │
└────────────┴────────────┴─────────┴────────────┴───┴────────────┴───────────┴───────────┴────────┘

### fill nans

In [7]:
mask = train_data.null_count().select(pl.all() > 0).to_numpy()[0].tolist()
cols_with_nans = [col for i, col in enumerate(train_data.columns) if mask[i]]
train_data.null_count().select(cols_with_nans)

shape: (1, 4)
┌─────┬────────────┬─────┬──────────────┐
│ age ┆ heart_rate ┆ BMI ┆ right atrium │
│ --- ┆ ---        ┆ --- ┆ ---          │
│ u32 ┆ u32        ┆ u32 ┆ u32          │
╞═════╪════════════╪═════╪══════════════╡
│ 6   ┆ 35         ┆ 565 ┆ 30           │
└─────┴────────────┴─────┴──────────────┘

In [8]:
base_estimator = CatBoostRegressor(
    random_state=0,
    iterations=100,
    learning_rate=0.05,
    depth=3,
)

In [9]:
imp_mean = IterativeImputer(
    random_state=0,
    estimator=base_estimator,
    initial_strategy="mean",
)
imp_mean.fit(
    train_data.select(
        pl.selectors.by_dtype(pl.Float64, pl.Int64, pl.Int32),
    )
    .drop("target")
    .to_pandas()
)
# imp_mean.transform(X)

0:	learn: 0.0706750	total: 55.9ms	remaining: 5.53s
1:	learn: 0.0705028	total: 56.4ms	remaining: 2.77s
2:	learn: 0.0703340	total: 56.8ms	remaining: 1.84s
3:	learn: 0.0701694	total: 57.1ms	remaining: 1.37s
4:	learn: 0.0698240	total: 57.4ms	remaining: 1.09s
5:	learn: 0.0696668	total: 57.7ms	remaining: 904ms
6:	learn: 0.0694155	total: 58.1ms	remaining: 772ms
7:	learn: 0.0692650	total: 58.4ms	remaining: 671ms
8:	learn: 0.0690255	total: 58.7ms	remaining: 593ms
9:	learn: 0.0688818	total: 59ms	remaining: 531ms
10:	learn: 0.0687413	total: 59.4ms	remaining: 480ms
11:	learn: 0.0686041	total: 59.7ms	remaining: 438ms
12:	learn: 0.0684700	total: 60ms	remaining: 402ms
13:	learn: 0.0683377	total: 60.4ms	remaining: 371ms
14:	learn: 0.0682098	total: 60.7ms	remaining: 344ms
15:	learn: 0.0680844	total: 61ms	remaining: 320ms
16:	learn: 0.0677861	total: 61.3ms	remaining: 299ms
17:	learn: 0.0676665	total: 61.6ms	remaining: 281ms
18:	learn: 0.0675496	total: 61.9ms	remaining: 264ms
19:	learn: 0.0673030	total: 

IterativeImputer(estimator=<catboost.core.CatBoostRegressor object at 0x1768f0e00>,
                 random_state=0)

In [10]:
values = imp_mean.transform(
    train_data.select(
        pl.selectors.by_dtype(pl.Float64, pl.Int64, pl.Int32),
    )
    .drop("target")
    .to_pandas()
)

In [11]:
filed_cols = pd.DataFrame(
    data=values,  # values
    #   index=data[1:,0],    # 1st column as index
    columns=train_data.select(
        pl.selectors.by_dtype(pl.Float64, pl.Int64, pl.Int32),
    )
    .drop("target")
    .columns,
)[cols_with_nans]

filed_cols.head(3)

age  heart_rate        BMI  right atrium
0  46.0        76.0  29.917068           3.5
1  54.0        77.0  37.000000           3.3
2  62.0        49.0  29.668337           3.4

In [12]:
train_data = train_data.with_columns(
    (
        pl.Series(
            name=col,
            values=filed_cols[col].round(1),
        )
        for col in filed_cols.columns
    )
)

In [13]:
mask = train_data.null_count().select(pl.all() > 0).to_numpy()[0].tolist()
cols_with_nans = [col for i, col in enumerate(train_data.columns) if mask[i]]
train_data.null_count().select(cols_with_nans)

shape: (0, 0)
┌┐
╞╡
└┘

In [14]:
path = "data_for_models"
os.makedirs(os.path.join(FILES_DIR, path), exist_ok=True)
file_name = "imputed_train_data.parquet"
file_path = os.path.join(FILES_DIR, path, file_name)
train_data.write_parquet(file_path)
# train_data = pl.read_parquet(file_path)

### split data

In [100]:
X_train, X_test, y_train, y_test = train_test_split(
    train_data.drop("target"),
    train_data["target"],
    test_size=0.2,
    random_state=1,
)

X_train, X_eval, y_train, y_eval = train_test_split(
    X_train,
    y_train,
    test_size=0.25,
    random_state=1,
)  # 0.25 x 0.8 = 0.2

In [104]:
cat_cols = X_train.select(
    pl.selectors.by_dtype(pl.String),
).columns

### catboost

In [114]:
model = CatBoostClassifier(
    random_seed=2024,
    cat_features=cat_cols,
    eval_metric="AUC",
    depth=3,
    iterations=500,
    learning_rate=0.06,
)

model.fit(
    X=X_train.to_pandas(),
    y=y_train.to_pandas(),
    early_stopping_rounds=50,
    verbose=True,
    eval_set=(
        X_eval.to_pandas(),
        y_eval.to_pandas(),
    ),
)

metric = roc_auc_score(y_test, model.predict_proba(X_test.to_pandas())[:, 1])
print(metric.round(3))

0:	test: 0.7010102	best: 0.7010102 (0)	total: 2.9ms	remaining: 1.44s
1:	test: 0.7130193	best: 0.7130193 (1)	total: 8.2ms	remaining: 2.04s
2:	test: 0.7250283	best: 0.7250283 (2)	total: 13.2ms	remaining: 2.19s
3:	test: 0.7178126	best: 0.7250283 (2)	total: 14.8ms	remaining: 1.83s
4:	test: 0.7221936	best: 0.7250283 (2)	total: 16.2ms	remaining: 1.6s
5:	test: 0.7221936	best: 0.7250283 (2)	total: 17.6ms	remaining: 1.45s
6:	test: 0.7755901	best: 0.7755901 (6)	total: 19.2ms	remaining: 1.35s
7:	test: 0.7761571	best: 0.7761571 (7)	total: 21.1ms	remaining: 1.3s
8:	test: 0.7768787	best: 0.7768787 (8)	total: 22.4ms	remaining: 1.22s
9:	test: 0.7768787	best: 0.7768787 (8)	total: 23.7ms	remaining: 1.16s
10:	test: 0.7772395	best: 0.7772395 (10)	total: 24.9ms	remaining: 1.11s
11:	test: 0.7760025	best: 0.7772395 (10)	total: 26.1ms	remaining: 1.06s
12:	test: 0.7684775	best: 0.7772395 (10)	total: 27.7ms	remaining: 1.04s
13:	test: 0.7684775	best: 0.7772395 (10)	total: 28.9ms	remaining: 1s
14:	test: 0.7688383

In [119]:
explainer = shap.TreeExplainer(model)
shap_values = explainer(X_train.to_pandas())
shap.plots.beeswarm(
    shap_values,
    plot_size=(8, 5),
)
plt.show()

### automl